In [2]:
import pandas as pd
import numpy as np
import random 
import plotly.graph_objects as go
from scipy.stats import norm

In [3]:
def bm_simulations(n_paths, granularity, max_time):
    n_steps = granularity * max_time
    
    paths = []
    for i in range(n_paths):
        xs = random.choices([-1, 1], weights = [0.5, 0.5], k = n_steps)
        xs = [0] + xs
        path = np.cumsum(xs)/np.sqrt(granularity)
        paths.append(path)
        
    return paths

$$V_t= \mu+\frac{\sigma}{\sqrt{2\theta}}e^{-\theta t} W_{e^{2\theta t}}$$
 
Using the method, proved in the article.

In [4]:
def Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t):
    
    t_=np.linspace(0,t, n*t+1)
    mult=sigma/np.sqrt(2*theta)*np.exp(-1*theta*t_)
    
    paths=[]
    for _ in range(N):
        OU_0=norm.rvs(loc=0, scale=sigma/np.sqrt(2*theta))
        OU_0_=OU_0/mult[0]
        W_phi=[OU_0_]
        for i in range(1,len(t_)):
            incr=norm.rvs(loc=0, scale=np.sqrt(np.exp(2*theta*t_[i])-np.exp(2*theta*t_[i-1])))
            W_phi.append(incr)
        
        W_phi=np.array(W_phi)
        W_phi=np.cumsum(W_phi)
        path=W_phi*mult+mu
        paths.append(path)
    return t_, paths

In [5]:
sigma=0.2
theta=1
mu=20
N=200
n=100
t=20



t_, paths_=Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t)
plot=go.Figure()
for i in paths_:
    graph=go.Scatter(x=t_, y=i)
    plot.add_trace(graph)
plot.show()

# Unit tests (Process validation)

In [6]:
sigma=0.6
theta=3
mu=0
N=30000
n=100
t=2

t_, paths=Ornstein_Ukhlenbeck(sigma, theta, mu, N, n, t)

X1_sample=[path[int(t*n/2)] for path in paths]
X1_bar=np.mean(X1_sample)
X1_var=np.var(X1_sample)


X2_sample=([path[-1] for path in paths])
X2_bar=np.mean(X2_sample)
X2_var=np.var(X2_sample)


X1_X2_cov=np.cov(X1_sample,X2_sample)


print(f'difference between E(X_10) practical and theoretical:{abs(X1_bar-mu)}')
print(f'difference between E(X_20) practical and theoretical:{abs(X2_bar-mu)}')
print(f'difference between Var(X_10) practical and theoretical:{abs(X1_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t/2)))}')
print(f'difference between Var(X_20) practical and theoretical:{abs(X2_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t)))}')

print(f'difference between Cov(X_10,X_20) practical and theoretical:{abs(X1_X2_cov[0,1]-sigma**2/(2*theta)*(np.exp(-theta*t/2)-np.exp(-theta*1.5*t)))}')


difference between E(X_10) practical and theoretical:1.731531114889432e-05
difference between E(X_20) practical and theoretical:0.0008053821942163055
difference between Var(X_10) practical and theoretical:0.000263185330654038
difference between Var(X_20) practical and theoretical:0.0002035373005831384
difference between Cov(X_10,X_20) practical and theoretical:0.0002850108812432416
